In [13]:
import operator
import csv
import math
import datetime
import snap
import random
import numpy as np

In [2]:
# Randomly determine if the node should be infected based on edge infect probability
def infectNode(Network, eid):
	p_infect = Network.GetFltAttrDatE(eid, 'p_infect')
	rndInt = random.uniform(0, 1)
	
	if rndInt < p_infect:
		return True

	return False

In [3]:
def loadDNCNetwork(filename, p_infect, p_infect_hardened, t_recover, detector_ids, hardened_ids):
	print 'Loading DNC Network'
	added = 0

	Network = snap.GenFull(snap.PNEANet, 0)
	print Network.GetNodes(), Network.GetEdges()
	with open(filename,'rb') as tsvin:
		tsvin = csv.reader(tsvin, delimiter='\t')
		i = 0 # Ignore header
		maxID = 0
		for row in tsvin:
			if i > 0:
				srcID = int(row[0])
				dstID = int(row[1])
				timestamp = int(row[3])
				if srcID > maxID:
					maxID = srcID
				if dstID > maxID:
					maxID = dstID
				
				# Add nodes to network if not already there
				if not Network.IsNode(srcID):
					added+=1
					Network.AddNode(srcID)
					# normal user or detector
					if srcID in detector_ids:
						Network.AddStrAttrDatN(srcID, 'detector', 'type')
					else:
						Network.AddStrAttrDatN(srcID, 'user', 'type')

				if not Network.IsNode(dstID):
					Network.AddNode(dstID)
					# normal user or detector
					if dstID in detector_ids:
						Network.AddStrAttrDatN(dstID, 'detector', 'type')
					else:
						Network.AddStrAttrDatN(dstID, 'user', 'type')

				# Add edge attributes (Note, multi edges allowed)
				eid = Network.AddEdge(srcID, dstID)
				Network.AddIntAttrDatE(eid, timestamp, 'timestamp')
				Network.AddIntAttrDatE(eid, t_recover, 't_recover')
				if dstID in hardened_ids:
					Network.AddFltAttrDatE(eid, p_infect_hardened, 'p_infect') #TODO: Do we need to distinguish between hardened/de
				else:
					Network.AddFltAttrDatE(eid, p_infect, 'p_infect')

				# state: infected or susceptible
				Network.AddStrAttrDatN(srcID, 'susceptible', 'state')
				Network.AddStrAttrDatN(dstID, 'susceptible', 'state')

			i+=1

	# Add any disjoint nodes (nodes without entries in the tsv file)
	for nID in range(maxID):
		if nID > 0 and not Network.IsNode(nID):
			Network.AddNode(nID)
			Network.AddStrAttrDatN(nID, 'susceptible', 'state')
			if nID in detector_ids:
				Network.AddStrAttrDatN(nID, 'detector', 'type')
			else:
				Network.AddStrAttrDatN(nID, 'user', 'type')


	print 'NUM NODES: ' + str(Network.GetNodes())
	print 'NUM EDGES: ' + str(Network.GetEdges())
	print 'NODES WITH OUTGOING EDGES: ' + str(added)
	return Network

In [5]:
# Marks k top nodes as detectors
def loadDetectorIds(rankingFilename, k):
	print 'Choosing ' + str(k) + ' detector ids'
	detector_ids = []
	with open(rankingFilename,'rb') as tsvin:
		tsvin = csv.reader(tsvin, delimiter='\t')
		i = 0
		for row in tsvin:
			if i >= (k + 1):
				break
			nID = int(row[0])
			detector_ids.append(nID)
			i+=1

	return detector_ids

In [7]:
filename = 'out.dnc-temporalGraph'
score_filename = 'socialScore.txt'
debug = True

In [8]:
# e-mails can have multiple timestamps
def orderTimestamps(filename):
    
    timestampsDict = dict()

    with open(filename,'rb') as tsvin:
        tsvin = csv.reader(tsvin, delimiter='\t')
        next(tsvin)
        
        for row in tsvin:
            srcID = int(row[0])
            dstID = int(row[1])
            timestamp = int(row[3])
            edge = (srcID, dstID, timestamp)
            if edge in timestampsDict:
                timestampsDict[edge] += 1
            else:
                timestampsDict[edge] = 1
    
    sorted_timestampsDict = sorted( (key[2], key[0], key[1], value) for (key, value) in timestampsDict.items() )
    
    
    return sorted_timestampsDict

In [32]:
p_initial_infect_params = [0.0005, 0.001, 0.005, 0.01, 0.05]
total_detectors_params = range(20, 250, 20)
p_infect_params = [ float(p) / 100 for p in range(5, 51, 5) ]

In [10]:
timestampsOrdered = orderTimestamps(filename)
del(timestampsOrdered[0])


In [21]:
timestampsOrdered[0][0]

1421071197

In [33]:
# TODO (maybe): Track cascasdes? add recovery time? take some nodes offline?
# input arguments: network, patient zeros, timestampsOrdered as produced by the orderTimestamps function, debug verbose command
# returns: time to alert, population affected, steps, outbreak successfully detected (1/0)
def outbreakTimestamp_gridSearch(Network, p_initial_infect, timestampsOrdered, debug=False ):
    print 'running timestamp model 2 by Andrew'

    # Creates different output for different executions
    Rnd = snap.TRnd(42)
    Rnd.Randomize()
    
    # Mark initial nodes infected
    num_nodes_infect = math.floor(Network.GetNodes() * p_initial_infect)
    cur_infected_ids = []
    detectors_alerted = []
    
    while len(cur_infected_ids) < num_nodes_infect:
        nID = Network.GetRndNId(Rnd) # TODO: make this return different values on every run
        if nID not in cur_infected_ids:
            cur_infected_ids.append(nID)
            Network.AddStrAttrDatN(nID, 'infected', 'state') # resets state
            if Network.GetStrAttrDatN(nID, 'type') == 'detector' and nID not in detectors_alerted:
                detectors_alerted.append(nID)


    num_nodes_infect = len(cur_infected_ids)
    print 'INITIAL SET OF INFECTED NODES Size: ' + str( len(cur_infected_ids) )
    
    if debug:
        print cur_infected_ids

    steps = 0
    found_earliest_infection = False # used to track time of first transmission of infection
    time_first_infection = timestampsOrdered[0][0] # first infection is at least from the first e-mail's time
    cur_time = timestampsOrdered[0][0]
    
    for timestamp in timestampsOrdered: # cycle thru the timestamps in the e-mails
        
        if len(detectors_alerted) >= 20: # 10 detectors triggered means an alert and end to the simulation
            print "Outbreak detected!"
            
            if debug:
                print "Detectors Alerted: "
                print detectors_alerted
                print "STEP: " + str(steps)
                print "TIME INITIAL INFECTION: " + str(time_first_infection) + " TIME DETECTION: " + str(cur_time)
                print "TIME TO DETECTION: " + str(time_to_detection)
            print "NUM INFECTED: " + str(len(cur_infected_ids))
            return cur_time - time_first_infection, len(cur_infected_ids) - num_nodes_infect, steps, 1
        
        if debug:
            if steps % 1000 == 0:
                print 'STEP: ' + str(steps)
                print 'CURRENTLY INFECTED: ' + str(cur_infected_ids)
                print 'DETECTORS ALERTED: ' + str(detectors_alerted) + '\n\n'
        
        cur_time = timestamp[0]
        sourceNode = timestamp[1]
        destNode = timestamp[2]
        
        eid = Network.GetEI(sourceNode, destNode)
        
        if sourceNode in cur_infected_ids: # need to chekc if our source node is infected before setting off detector
            if Network.GetStrAttrDatN(destNode, 'type') == 'detector':
                if destNode not in detectors_alerted:
                    detectors_alerted.append(destNode)
                                              
        infected = False # we are seeing if this edge can infect another node
        if sourceNode in cur_infected_ids: # let's trying to infect others if source node is infected
            for _ in range(timestamp[3]): # since an edge w/ the same timestamp can occur multiple times
                if not found_earliest_infection: # use the first infected e-mail transmission to track the start of the infection
                    time_first_infection = cur_time
                    found_earliest_infection = True
                if infectNode(Network, eid): # probabilistic infection happens here
                    infected = True
                    break # b/c we do have an infection
        
        if infected: # let's add another infected node
            if destNode not in cur_infected_ids:
                cur_infected_ids.append(destNode)
                Network.AddStrAttrDatN(destNode, 'infected', 'state')
        steps += 1

    print 'NO OUTBREAK DETECTED'
    return cur_time - time_first_infection, len(cur_infected_ids) - num_nodes_infect, steps, 0

In [34]:
gridSearch_results_f = open("gridSearch_results_intermediate20.txt", "w")

for p_initial_infect in p_initial_infect_params:
    for total_detectors in total_detectors_params: 
        for p_infect in p_infect_params:
            
            print('\n\n\n-------------------------------------------\nNew Set of Parameters\n')
            print "P_initial_infect = " + str(p_initial_infect)
            print "\nTotal Detectors = " + str(total_detectors)
            print "\nProbability of infecting neighbor = " + str(p_infect)

            detector_ids = loadDetectorIds('socialScore.txt', total_detectors)
            N = loadDNCNetwork(filename, p_infect, p_infect, 30, detector_ids, detector_ids) # customized graph

            
            for i in range(10):
                time_to_detection, num_infected_nodes, steps, outbreak_detected = outbreakTimestamp_gridSearch(N, p_initial_infect, timestampsOrdered, False)
                
                results = [p_initial_infect, total_detectors, p_infect, str( datetime.timedelta(seconds = time_to_detection ) ), num_infected_nodes, steps, outbreak_detected]
            
                print "Results for this set of parameters on Trial run: " + str(i)
                
                for item in results:
                    print item
                    gridSearch_results_f.write(str(item) + '\t') # write the result out to the file
                gridSearch_results_f.write('\n') 
                print '\n'
            
            
           
                




-------------------------------------------
New Set of Parameters

P_initial_infect = 0.0005

Total Detectors = 20

Probability of infecting neighbor = 0.05
Choosing 20 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 0
0.0005
20
0.05
11 days, 22:43:12
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 1
0.0005
20
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.0005
20
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 3
0.0005

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 8
0.0005
20
0.2
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 9
0.0005
20
0.2
498 days, 19:26:31
0
32879
0





-------------------------------------------
New Set of Parameters

P_initial_infect = 0.0005

Total Detectors = 20

Probability of infecting neighbor = 0.25
Choosing 20 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 0
0.0005
20
0.25
27 days, 4:24:03
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM INFECTED: 65
Results for this set of parameters on Trial run: 1
0.0005
20
0.25
11 days, 4:22:12
64
30224
1


running timestamp model

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 6
0.0005
20
0.4
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 7
0.0005
20
0.4
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 8
0.0005
20
0.4
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM INFECTED: 56
Results for this set of parameters on Trial run: 9
0.0005
20
0.4
3 days, 0:07:41
55
14878
1





-------------------------------------------
New Set of Parameters

P_initial_infect = 0.0005

Total Detectors = 20

Probability of infecting neighbor = 0.45
Choosing 20 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 5
0.0005
40
0.1
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 6
0.0005
40
0.1
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 7
0.0005
40
0.1
28 days, 7:01:59
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 8
0.0005
40
0.1
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 9
0.0005
40
0.1
26 days, 13:45:00
0
32879
0





-------------------------------------------
New Set of Parameters

P_initial_infect = 0.0005

Total Detectors = 40

Pro

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.0005
40
0.3
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 3
0.0005
40
0.3
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 4
0.0005
40
0.3
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM INFECTED: 43
Results for this set of parameters on Trial run: 5
0.0005
40
0.3
2 days, 5:01:42
42
5547
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 6
0.0005
40
0.3
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for 

...

Outbreak detected!
NUM INFECTED: 101
Results for this set of parameters on Trial run: 7
0.05
220
0.05
292 days, 21:09:32
0
2522
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 106
Results for this set of parameters on Trial run: 8
0.05
220
0.05
295 days, 19:17:24
5
531
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 106
Results for this set of parameters on Trial run: 9
0.05
220
0.05
298 days, 15:01:15
5
539
1





-------------------------------------------
New Set of Parameters

P_initial_infect = 0.05

Total Detectors = 220

Probability of infecting neighbor = 0.1
Choosing 220 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 102
Results for this set of parameters on Trial run: 0
0.05
220
0.1
443 d

NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 0
0.05
220
0.3
61 days, 22:07:08
6
183
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 1
0.05
220
0.3
254 days, 23:19:12
6
1805
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 103
Results for this set of parameters on Trial run: 2
0.05
220
0.3
0:00:00
2
158
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 106
Results for this set of parameters on Trial run: 3
0.05
220
0.3
303 days, 23:16:57
5
1836
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results f

NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 116
Results for this set of parameters on Trial run: 0
0.05
220
0.5
123 days, 20:58:29
15
58
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 110
Results for this set of parameters on Trial run: 1
0.05
220
0.5
253 days, 13:11:43
9
1669
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 2
0.05
220
0.5
454 days, 17:09:18
6
1650
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 3
0.05
220
0.5
382 days, 1:27:17
6
1618
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 1

NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 112
Results for this set of parameters on Trial run: 0
0.05
240
0.2
235 days, 21:58:07
11
1629
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 103
Results for this set of parameters on Trial run: 1
0.05
240
0.2
261 days, 20:42:38
2
1737
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 105
Results for this set of parameters on Trial run: 2
0.05
240
0.2
237 days, 14:11:06
4
1952
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 3
0.05
240
0.2
382 days, 18:23:20
6
1699
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED

NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 108
Results for this set of parameters on Trial run: 0
0.05
240
0.4
262 days, 1:55:10
7
1834
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 105
Results for this set of parameters on Trial run: 1
0.05
240
0.4
277 days, 20:19:07
4
371
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 117
Results for this set of parameters on Trial run: 2
0.05
240
0.4
218 days, 18:51:06
16
1471
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 112
Results for this set of parameters on Trial run: 3
0.05
240
0.4
221 days, 21:28:19
11
539
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 

In [205]:
grid_search_results

[[0.0005, 10, 0.05, 0.05, '251 days, 7:55:32.200000', 0.0, 24993.4, 0.4],
 [0.0005, 10, 0.05, 0.1, '225 days, 4:47:24.200000', 0.0, 28875.7, 0.2],
 [0.0005, 10, 0.05, 0.15, '167 days, 15:42:13.100000', 0.2, 29924.1, 0.1],
 [0.0005, 10, 0.05, 0.2, '200 days, 23:50:32.400000', 0.5, 25597.8, 0.4],
 [0.0005, 10, 0.05, 0.25, '206 days, 3:25:26.400000', 0.3, 29638.9, 0.3],
 [0.0005, 10, 0.05, 0.3, '252 days, 4:53:09.200000', 0.3, 31097.2, 0.3],
 [0.0005, 10, 0.05, 0.35, '301 days, 12:24:25.700000', 0.2, 26323.0, 0.3],
 [0.0005, 10, 0.05, 0.4, '255 days, 20:50:07.300000', 0.6, 24752.6, 0.3],
 [0.0005, 10, 0.05, 0.45, '252 days, 3:11:57.900000', 0.5, 25520.5, 0.4],
 [0.0005, 10, 0.05, 0.5, '199 days, 13:00:32.300000', 0.7, 20429.2, 0.6],
 [0.0005, 10, 0.1, 0.05, '351 days, 20:07:16.200000', 0.0, 29525.8, 0.2],
 [0.0005, 10, 0.1, 0.1, '134 days, 4:17:13.500000', 0.2, 28251.1, 0.4],
 [0.0005, 10, 0.1, 0.15, '203 days, 4:01:58.200000', 0.6, 22990.9, 0.4],
 [0.0005, 10, 0.1, 0.2, '204 days, 17:55:

In [200]:
import pickle

In [206]:
with open('grid_search_intermediate', 'w') as f1:
    pickle.dump(grid_search_results, f1)

In [24]:
str( datetime.timedelta(seconds = 19330808) )

'223 days, 17:40:08'

In [35]:
len(timestampsOrdered)

32879

# only vary p_infect

In [36]:
p_infect_params = [ float(p) / 100 for p in range(5, 51, 5) ]

In [40]:
gridSearch_results_f = open("gridSearch_results_pInfect_125detectors_1e-3initial.txt", "w")
for p_infect in p_infect_params:     
    print('\n\n\n-------------------------------------------\nVarying P_Infect\n')
    print "\nProbability of infecting neighbor = " + str(p_infect)

    detector_ids = loadDetectorIds('socialScore.txt', 125)
    N = loadDNCNetwork(filename, p_infect, p_infect, 30, detector_ids, detector_ids) # customized graph


    for i in range(200):
        time_to_detection, num_infected_nodes, steps, outbreak_detected = outbreakTimestamp_gridSearch(N, 1e-3, timestampsOrdered, False)

        results = [1e-3, 125, p_infect, str( datetime.timedelta(seconds = time_to_detection ) ), num_infected_nodes, steps, outbreak_detected]

        print "Results for this set of parameters on Trial run: " + str(i)

        for item in results:
            print item
            gridSearch_results_f.write(str(item) + '\t') # write the result out to the file
        gridSearch_results_f.write('\n') 
        print '\n'

gridSearch_results_f.close()




-------------------------------------------
Varying P_Infect


Probability of infecting neighbor = 0.05
Choosing 125 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 0
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 1
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.001
125
0.05
27 days, 3:57:33
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 11
Results for this set of parameters on Trial run: 3
0.001
125
0.05
3 days, 21:02:18
9
17550
1




Outbreak detected!
NUM INFECTED: 9
Results for this set of parameters on Trial run: 42
0.001
125
0.05
29 days, 9:09:51
7
32793
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 43
0.001
125
0.05
209 days, 2:04:36
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 44
0.001
125
0.05
20 days, 14:55:01
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 45
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 46
0.001
125
0.05
29 days, 21:32:06
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Resul

Outbreak detected!
NUM INFECTED: 8
Results for this set of parameters on Trial run: 86
0.001
125
0.05
2:24:25
6
2695
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 87
0.001
125
0.05
5 days, 20:17:09
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 88
0.001
125
0.05
15 days, 19:53:53
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 89
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 90
0.001
125
0.05
2 days, 20:20:40
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this 

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 130
0.001
125
0.05
4 days, 17:53:53
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 14
Results for this set of parameters on Trial run: 131
0.001
125
0.05
5 days, 19:31:59
12
9913
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 132
0.001
125
0.05
29 days, 23:56:52
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 133
0.001
125
0.05
30 days, 18:20:46
2
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 134
0.001
125
0.05
2 days, 3:22:51
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM I

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 173
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 174
0.001
125
0.05
29 days, 19:24:35
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 7
Results for this set of parameters on Trial run: 175
0.001
125
0.05
10 days, 3:30:59
5
14208
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 176
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 177
0.001
125
0.05
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTE

...

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 11
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 12
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 23
Results for this set of parameters on Trial run: 13
0.001
125
0.5
217 days, 1:36:02
21
2560
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 30
Results for this set of parameters on Trial run: 14
0.001
125
0.5
19:29:18
28
25267
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 15
0.001
125
0.5
1 day, 16:44:36
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM 

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 56
0.001
125
0.5
25 days, 19:09:49
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 27
Results for this set of parameters on Trial run: 57
0.001
125
0.5
23:19:34
25
3386
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 58
0.001
125
0.5
24 days, 1:46:12
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 59
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 60
0.001
125
0.5
1 day, 23:47:19
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 99
0.001
125
0.5
5 days, 15:20:46
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 100
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 101
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 102
0.001
125
0.5
27 days, 3:57:33
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 49
Results for this set of parameters on Trial run: 103
0.001
125
0.5
163 days, 22:10:36
47
28212
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM I

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 142
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 22
Results for this set of parameters on Trial run: 143
0.001
125
0.5
7:02:02
20
3334
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 30
Results for this set of parameters on Trial run: 144
0.001
125
0.5
12:50:45
28
22195
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 145
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 146
0.001
125
0.5
441 days, 8:16:01
3
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INF

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 187
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 188
0.001
125
0.5
216 days, 20:24:52
2
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 31
Results for this set of parameters on Trial run: 189
0.001
125
0.5
2 days, 3:24:19
29
7222
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 190
0.001
125
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 191
0.001
125
0.5
6 days, 3:06:09
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Resul

# only vary total detectors

In [41]:
gridSearch_results_f = open("gridSearch_results_totalDetectors_0.25pInfect_1e-3initial.txt", "w")
for total_detectors in total_detectors_params:     
    print('\n\n\n-------------------------------------------\nVarying Total Detectors\n')
    print "\nTotal Detectors = " + str(total_detectors)

    detector_ids = loadDetectorIds('socialScore.txt', total_detectors)
    N = loadDNCNetwork(filename, 0.25, 0.25, 30, detector_ids, detector_ids) # customized graph


    for i in range(200):
        time_to_detection, num_infected_nodes, steps, outbreak_detected = outbreakTimestamp_gridSearch(N, 1e-3, timestampsOrdered, False)

        results = [1e-3, total_detectors, p_infect, str( datetime.timedelta(seconds = time_to_detection ) ), num_infected_nodes, steps, outbreak_detected]

        print "Results for this set of parameters on Trial run: " + str(i)

        for item in results:
            print item
            gridSearch_results_f.write(str(item) + '\t') # write the result out to the file
        gridSearch_results_f.write('\n') 
        print '\n'

gridSearch_results_f.close()




-------------------------------------------
Varying Total Detectors


Total Detectors = 20
Choosing 20 detector ids
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 0
0.001
20
0.5
2 days, 14:57:52
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 82
Results for this set of parameters on Trial run: 1
0.001
20
0.5
12 days, 13:26:54
80
19814
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.001
20
0.5
21 days, 10:26:23
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 3
0.001
20
0.5
4 days, 22:21:09
0
32879
0


running timestamp model

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 42
0.001
20
0.5
29 days, 20:20:53
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 118
Results for this set of parameters on Trial run: 43
0.001
20
0.5
4 days, 13:39:21
116
8365
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 44
0.001
20
0.5
20 days, 23:42:54
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 45
0.001
20
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 46
0.001
20
0.5
5 days, 20:17:09
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 4

Outbreak detected!
NUM INFECTED: 95
Results for this set of parameters on Trial run: 85
0.001
20
0.5
6 days, 0:17:47
93
8747
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 155
Results for this set of parameters on Trial run: 86
0.001
20
0.5
3 days, 20:48:12
153
7802
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 87
0.001
20
0.5
15 days, 17:46:51
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 88
0.001
20
0.5
27 days, 19:43:22
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 89
0.001
20
0.5
1 day, 23:47:39
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Re

Outbreak detected!
NUM INFECTED: 82
Results for this set of parameters on Trial run: 128
0.001
20
0.5
5 days, 7:01:18
80
8546
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 53
Results for this set of parameters on Trial run: 129
0.001
20
0.5
3 days, 0:45:37
51
28835
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 102
Results for this set of parameters on Trial run: 130
0.001
20
0.5
4 days, 23:36:14
100
7727
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 109
Results for this set of parameters on Trial run: 131
0.001
20
0.5
3 days, 0:09:32
107
29774
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 132
0.001
20
0.5
16 days, 1:24:18
16
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED 

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 172
0.001
20
0.5
19 days, 1:19:47
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 173
0.001
20
0.5
12 days, 19:31:22
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 174
0.001
20
0.5
4 days, 19:15:46
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 175
0.001
20
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 176
0.001
20
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of 

...

NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 12
Results for this set of parameters on Trial run: 0
0.001
240
0.5
2 days, 3:41:23
10
7076
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 13
Results for this set of parameters on Trial run: 1
0.001
240
0.5
10 days, 21:49:30
11
25104
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.001
240
0.5
24 days, 0:23:02
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 3
0.001
240
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 27
Results for this set of parameters on

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 44
0.001
240
0.5
1 day, 13:46:34
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 14
Results for this set of parameters on Trial run: 45
0.001
240
0.5
1 day, 14:15:17
12
12456
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 46
0.001
240
0.5
27 days, 23:43:23
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 47
0.001
240
0.5
7 days, 23:06:46
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 15
Results for this set of parameters on Trial run: 48
0.001
240
0.5
270 days, 9:15:09
13
18029
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 89
0.001
240
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 16
Results for this set of parameters on Trial run: 90
0.001
240
0.5
4:54:29
14
16190
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 14
Results for this set of parameters on Trial run: 91
0.001
240
0.5
13:37:27
12
3749
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 12
Results for this set of parameters on Trial run: 92
0.001
240
0.5
1 day, 2:43:18
10
4365
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 93
0.001
240
0.5
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTE

Outbreak detected!
NUM INFECTED: 16
Results for this set of parameters on Trial run: 132
0.001
240
0.5
191 days, 19:11:42
14
23816
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 22
Results for this set of parameters on Trial run: 133
0.001
240
0.5
1 day, 22:27:34
20
6501
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 134
0.001
240
0.5
19 days, 1:19:47
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 25
Results for this set of parameters on Trial run: 135
0.001
240
0.5
5 days, 19:40:00
23
26892
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 9
Results for this set of parameters on Trial run: 136
0.001
240
0.5
1 day, 1:02:18
7
5816
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED 

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 174
0.001
240
0.5
20 days, 16:51:30
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 12
Results for this set of parameters on Trial run: 175
0.001
240
0.5
13:16:09
10
13980
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 23
Results for this set of parameters on Trial run: 176
0.001
240
0.5
21 days, 5:39:42
21
27945
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 177
0.001
240
0.5
18 days, 19:22:42
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
Outbreak detected!
NUM INFECTED: 18
Results for this set of parameters on Trial run: 178
0.001
240
0.5
237 days, 12:31:19
16
10515
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 2
N

# only vary p_initial_infect

In [42]:
gridSearch_results_f = open("gridSearch_results_totalDetectors_0.25pInfect_200detectors.txt", "w")
detector_ids = loadDetectorIds('socialScore.txt', 200)
for p_initial_infect in p_initial_infect_params:     
    print('\n\n\n-------------------------------------------\nVarying P_initial_infect\n')
    print "P_initial_infect = " + str(p_initial_infect)

    
    N = loadDNCNetwork(filename, 0.25, 0.25, 30, detector_ids, detector_ids) # customized graph


    for i in range(200):
        time_to_detection, num_infected_nodes, steps, outbreak_detected = outbreakTimestamp_gridSearch(N, p_initial_infect, timestampsOrdered, False)

        results = [p_initial_infect, 200, 0.25, str( datetime.timedelta(seconds = time_to_detection ) ), num_infected_nodes, steps, outbreak_detected]

        print "Results for this set of parameters on Trial run: " + str(i)

        for item in results:
            print item
            gridSearch_results_f.write(str(item) + '\t') # write the result out to the file
        gridSearch_results_f.write('\n') 
        print '\n'

gridSearch_results_f.close()

Choosing 200 detector ids



-------------------------------------------
Varying P_initial_infect

P_initial_infect = 0.0005
Loading DNC Network
0 0
NUM NODES: 2029
NUM EDGES: 39264
NODES WITH OUTGOING EDGES: 796
running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 0
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 1
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 2
0.0005
200
0.25
28 days, 21:56:13
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM INFECTED: 13
Results for this set of parameters on Trial run: 3
0.0005
200
0.25
1 day, 23:29:49
12
2320
1


runn

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 43
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 44
0.0005
200
0.25
26 days, 9:18:47
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 45
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 46
0.0005
200
0.25
1 day, 23:48:33
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 47
0.0005
200
0.25
29 days, 23:24:53
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for thi

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 85
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 86
0.0005
200
0.25
14 days, 16:38:40
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 87
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 88
0.0005
200
0.25
27 days, 23:17:48
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 89
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM INFECTED:

Outbreak detected!
NUM INFECTED: 8
Results for this set of parameters on Trial run: 127
0.0005
200
0.25
13:48:04
7
27095
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 128
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 129
0.0005
200
0.25
5 days, 8:56:12
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 130
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 131
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
Outbreak detected!
NUM I

NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 171
0.0005
200
0.25
6 days, 1:31:49
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 172
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 173
0.0005
200
0.25
14:57:35
1
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 174
0.0005
200
0.25
498 days, 19:26:31
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this set of parameters on Trial run: 175
0.0005
200
0.25
26 days, 22:08:39
0
32879
0


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 1
NO OUTBREAK DETECTED
Results for this s

...

Outbreak detected!
NUM INFECTED: 28
Results for this set of parameters on Trial run: 182
0.01
200
0.25
348 days, 0:44:18
8
4183
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 20
Outbreak detected!
NUM INFECTED: 30
Results for this set of parameters on Trial run: 183
0.01
200
0.25
23 days, 22:10:46
10
28306
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 20
Outbreak detected!
NUM INFECTED: 39
Results for this set of parameters on Trial run: 184
0.01
200
0.25
13:40:13
19
3079
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 20
Outbreak detected!
NUM INFECTED: 31
Results for this set of parameters on Trial run: 185
0.01
200
0.25
2 days, 9:44:41
11
5877
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 20
Outbreak detected!
NUM INFECTED: 30
Results for this set of parameters on Trial run: 186
0.01
200
0.25
1 day, 6:40:43
10
4706
1


running timestamp model 2 by Andrew
INITIAL SET O

Outbreak detected!
NUM INFECTED: 114
Results for this set of parameters on Trial run: 24
0.05
200
0.25
441 days, 1:42:38
13
1555
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 106
Results for this set of parameters on Trial run: 25
0.05
200
0.25
218 days, 1:04:35
5
2028
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 111
Results for this set of parameters on Trial run: 26
0.05
200
0.25
103 days, 2:19:50
10
51
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 109
Results for this set of parameters on Trial run: 27
0.05
200
0.25
441 days, 10:25:57
8
1625
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 104
Results for this set of parameters on Trial run: 28
0.05
200
0.25
61 days, 19:48:54
3
551
1


running timestamp model 2 by Andrew


Outbreak detected!
NUM INFECTED: 105
Results for this set of parameters on Trial run: 72
0.05
200
0.25
199 days, 12:59:50
4
1658
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 105
Results for this set of parameters on Trial run: 73
0.05
200
0.25
261 days, 15:39:38
4
1969
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 74
0.05
200
0.25
442 days, 8:57:55
6
1832
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 115
Results for this set of parameters on Trial run: 75
0.05
200
0.25
177 days, 23:21:36
14
2013
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 114
Results for this set of parameters on Trial run: 76
0.05
200
0.25
234 days, 0:53:23
13
164
1


running timestamp model 2 by And

Outbreak detected!
NUM INFECTED: 106
Results for this set of parameters on Trial run: 119
0.05
200
0.25
215 days, 0:16:00
5
2360
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 109
Results for this set of parameters on Trial run: 120
0.05
200
0.25
257 days, 20:53:53
8
2936
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 103
Results for this set of parameters on Trial run: 121
0.05
200
0.25
266 days, 18:50:56
2
1499
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 104
Results for this set of parameters on Trial run: 122
0.05
200
0.25
206 days, 1:43:35
3
1839
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 103
Results for this set of parameters on Trial run: 123
0.05
200
0.25
292 days, 21:03:13
2
2496
1


running timestamp model 2 by

Outbreak detected!
NUM INFECTED: 114
Results for this set of parameters on Trial run: 167
0.05
200
0.25
257 days, 17:19:15
13
2421
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 116
Results for this set of parameters on Trial run: 168
0.05
200
0.25
196 days, 0:42:52
15
3888
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 108
Results for this set of parameters on Trial run: 169
0.05
200
0.25
390 days, 0:44:24
7
2511
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 107
Results for this set of parameters on Trial run: 170
0.05
200
0.25
214 days, 1:02:49
6
2184
1


running timestamp model 2 by Andrew
INITIAL SET OF INFECTED NODES Size: 101
Outbreak detected!
NUM INFECTED: 103
Results for this set of parameters on Trial run: 171
0.05
200
0.25
214 days, 0:27:15
2
606
1


running timestamp model 2 by 